In [1]:
%pip install numpy tqdm

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.6/57.6 kB 935.9 kB/s eta 0:00:00 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.3/78.3 kB 629.7 kB/s eta 0:00:00a 0:00:01

[notice] A new release of pip is available: 23.3.1 -> 23.3.2
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [1]:
import os
from typing import Tuple, List, Union, Dict
from collections import defaultdict
import numpy as np
import re
import math
import itertools
from tqdm import tqdm

In [2]:
def number_string_to_int_list(s: str) -> List[int]:
    return [int(c) for c in s.split(" ") if c.lstrip(" ")]

# Day 1

In [46]:

def first_digit_char(s: str) -> Tuple[int, int]:
    for i, c in enumerate(s):
        if c.isdigit():
            return i,int(c)
    raise Exception(f"No digit found in {s}")

def solve(lines) -> int:
    total_sum = 0
    for line in lines:
        number = int(f"{first_digit_char(line)[1]}{first_digit_char(reversed(line))[1]}")
        total_sum += number
    return total_sum

with open("input_day_1") as f:
    total_sum = solve(f)
        
print("Total sum is", total_sum)

Total sum is 55834


## Part 2

In [47]:
digits = ("one", "two", "three", "four", "five", "six", "seven", "eight", "nine")

def first_digit_word(s: str, digits: List[str]) -> Tuple[int,int]:
    min_pair = (len(s), None)
    for i,d in enumerate(digits):
        idx = s.find(d)
        if idx != -1 and idx < min_pair[0]:
            min_pair = (idx, i+1)
    return min_pair


def solve(lines) -> int:
    total_sum = 0
    for line in lines:
        _, d1 = min(first_digit_char(line),first_digit_word(line, digits), key=lambda t: t[0])

        line_reversed = line[::-1]
        digits_reversed = [d[::-1] for d in digits]
        _, d2 = min(first_digit_char(line_reversed),first_digit_word(line_reversed, digits_reversed), key=lambda t: t[0])

        number = int(f"{d1}{d2}")
        total_sum += number
    return total_sum

with open("input_day_1") as f:
    total_sum = solve(f)

print("Total Sum", total_sum)

Total Sum 53221


# Day 2

In [48]:


def game_string_to_dict(game_str: str) -> dict[str, int]:
    game, sets = game_str.split(": ")
    game_id = int(game.split(" ")[1])
    sets = sets.split("; ")

    game_stats = defaultdict(int)
    game_stats["Game_ID"] = game_id

    for set_string in sets:
        for color in set_string.split(", "):
            v,k = color.split(" ")
            assert k in ("red", "green", "blue"), f"not in colors '{k}'"
            game_stats[k] = max(int(v), game_stats[k])
    return game_stats

id_sum = 0
with open("input_day_2") as f:
    for r in f:
        r = r.rstrip("\n")
        game = game_string_to_dict(r)
        if game["red"] <= 12 and game["green"] <= 13 and game["blue"] <= 14:
            id_sum += game["Game_ID"]
print("Total sum of filtered Game IDs", id_sum)    

Total sum of filtered Game IDs 2348


In [49]:
from functools import reduce
from operator import mul


prod_sum = 0
with open("input_day_2") as f:
    for r in f:
        r = r.rstrip("\n")
        game = game_string_to_dict(r)
        cubes = [c for c in [game["red"], game["blue"], game["green"]] if c > 0]
        prod_sum += reduce(mul, cubes, 1)
print("Total sum of products of games", prod_sum)

Total sum of products of games 76008


# Day 3

In [50]:
def parse_numbers_and_symbol_indezes(s: str) -> Tuple[Dict[Tuple[int, int], str], Dict[Tuple[int, int], str]]:
    numbers_indezes = dict() # key is inex (row, end_col), value is number
    symbol_indezes = dict() # key is index (row, col), value is symbol

    for row_idx, row in enumerate(s):
        current_number_seq = ""
        row = row.rstrip("\n")
        for i, c in enumerate(row):
            if c.isdigit():
                current_number_seq += c
            else:
                if current_number_seq:
                    numbers_indezes[(row_idx, i-1)]=current_number_seq
                    current_number_seq = ""
                if c != ".":
                    symbol_indezes[(row_idx, i)] = c
        if current_number_seq:
            numbers_indezes[(row_idx, i)]=current_number_seq
    return numbers_indezes, symbol_indezes

def compute_neighbour_symbols(numbers_indezes: Dict[Tuple[int, int], str], symbol_indezes: Dict[Tuple[int, int], str]) -> Tuple[Dict[Tuple[int, int], Tuple[str, Dict[Tuple[int, int], str]]], Dict[Tuple[int, int], Tuple[str, Dict[Tuple[int, int], str]]]]:
    numbers_with_neighbour_symbols: Dict[Tuple[int, int], Tuple[str, Dict[Tuple[int, int], str]]] = dict()
    symbols_with_neighbour_numbers: Dict[Tuple[int, int], Tuple[str, Dict[Tuple[int, int], str]]] = {
        idxs: (symbol, dict()) for idxs, symbol in symbol_indezes.items()
    }
    for (row_idx, end_index), num in sorted(numbers_indezes.items(), key=lambda t: t[0]):
        # neighbours are indezes 1 cells around the number, including diagonals
        # note that the number begins at end_index-len(num)+1
        neighbours = [(row_idx, end_index-len(num)), (row_idx, end_index+1)]
        for ic in (row_idx-1, row_idx+1):
            for j in range(end_index-len(num), end_index+2):
                neighbours.append((ic,j))

        numbers_with_neighbour_symbols[(row_idx, end_index)] = (num, dict())
        for ic,j in neighbours:
            if (ic,j) in symbol_indezes:
                numbers_with_neighbour_symbols[(row_idx, end_index)][1][(ic,j)] = symbol_indezes[(ic,j)]
                symbols_with_neighbour_numbers[(ic,j)][1][(row_idx, end_index)] = num
    return numbers_with_neighbour_symbols, symbols_with_neighbour_numbers


def compute_product_number_sum(numbers_with_neighbour_symbols: Dict[Tuple[int, int], Tuple[str, Dict[Tuple[int, int], str]]]) -> int:
    product_num_sum = 0
    for (row_idx, end_index), (num, symbols) in sorted(numbers_with_neighbour_symbols.items(), key=lambda t: t[0]):
        if len(symbols):
            print("Valid serial number", num, "at", row_idx, end_index-len(num)+1)
            product_num_sum += int(num)
        # else:
        #     print(f"No symbol found for number {num} at {(row_idx, end_index)}")
    return product_num_sum

def compute_gear_ratio_sum(symbols_with_neighbour_numbers: Dict[Tuple[int, int], Tuple[str, Dict[Tuple[int, int], str]]]) -> int:
    gear_ratio_sum = 0
    for (row_idx, col_idx), (symbol, numbers) in sorted(symbols_with_neighbour_numbers.items(), key=lambda t: t[0]):
        # if symbol is '*' and has exactly 2 neighbouring numbers, compute the gear ratio
        if symbol == "*" and len(numbers) == 2:
            gear_ratio = 1
            for num in numbers.values():
                gear_ratio *= int(num)
            gear_ratio_sum += gear_ratio
    return gear_ratio_sum

with open("input_day_3") as f:
    numbers_indezes, symbol_indezes = parse_numbers_and_symbol_indezes(f)
    numbers_with_neighbour_symbols, symbols_with_neighbour_numbers = compute_neighbour_symbols(numbers_indezes, symbol_indezes)
    print("Sum of products of numbers", compute_product_number_sum(numbers_with_neighbour_symbols))
    print("Sum of gear ratios", compute_gear_ratio_sum(symbols_with_neighbour_numbers))

Valid serial number 577 at 0 25
Valid serial number 56 at 0 90
Valid serial number 446 at 0 102
Valid serial number 793 at 0 106
Valid serial number 627 at 1 52
Valid serial number 623 at 1 76
Valid serial number 610 at 1 85
Valid serial number 16 at 1 124
Valid serial number 891 at 1 132
Valid serial number 336 at 2 21
Valid serial number 470 at 2 31
Valid serial number 84 at 2 57
Valid serial number 34 at 2 70
Valid serial number 76 at 2 95
Valid serial number 117 at 3 1
Valid serial number 359 at 3 7
Valid serial number 595 at 3 27
Valid serial number 129 at 3 42
Valid serial number 963 at 3 47
Valid serial number 722 at 3 53
Valid serial number 128 at 3 66
Valid serial number 192 at 3 77
Valid serial number 313 at 3 81
Valid serial number 31 at 3 92
Valid serial number 887 at 3 102
Valid serial number 234 at 3 120
Valid serial number 298 at 4 12
Valid serial number 922 at 4 20
Valid serial number 482 at 4 34
Valid serial number 395 at 4 97
Valid serial number 166 at 4 131
Valid ser

In [51]:
with open("input_day_3") as f:
    arr = f.readlines()

def is_symbol(row, col) -> bool:
    # check bounds
    if row < 0 or row >= len(arr) or col < 0 or col >= len(arr[row]) -1:
        return False
    # must be not digit or dot
    if not arr[row][col].isdigit() and arr[row][col] != ".":
        return True

def has_symbol_neighbour(row, col) -> bool:
    # check neighbours
    for i in range(row-1, row+2):
        for j in range(col-1, col+2):
            if is_symbol(i,j):
                return True
    return False

# find all numbers in the array
prod_sum = 0
for ir,r in enumerate(arr):
    number_seq = ""
    found_neighbour_symbol = False
    r = r.rstrip("\n")
    for ic, c in enumerate(r):
        if c.isdigit():
            number_seq += c
            if has_symbol_neighbour(ir, ic):
                found_neighbour_symbol = True
        elif number_seq:
            # terminate number sequence
            if found_neighbour_symbol:
                prod_sum += int(number_seq)
                print("Valid serial number", number_seq, "at", ir, ic-len(number_seq))
                found_neighbour_symbol = False
            # else: 
            #     print("Did not find symbol neighbour for number", number_seq, "at", (ir, ic-len(number_seq)))
            number_seq = ""
    # at end of row, check if number sequence is valid
    if number_seq and found_neighbour_symbol:
        print("Valid serial number", number_seq, "at", ir, ic-len(number_seq))
        prod_sum += int(number_seq)

print("Sum of products of numbers", prod_sum)


Valid serial number 577 at 0 25
Valid serial number 56 at 0 90
Valid serial number 446 at 0 102
Valid serial number 793 at 0 106
Valid serial number 627 at 1 52
Valid serial number 623 at 1 76
Valid serial number 610 at 1 85
Valid serial number 16 at 1 124
Valid serial number 891 at 1 132
Valid serial number 336 at 2 21
Valid serial number 470 at 2 31
Valid serial number 84 at 2 57
Valid serial number 34 at 2 70
Valid serial number 76 at 2 95
Valid serial number 117 at 3 1
Valid serial number 359 at 3 7
Valid serial number 595 at 3 27
Valid serial number 129 at 3 42
Valid serial number 963 at 3 47
Valid serial number 722 at 3 53
Valid serial number 128 at 3 66
Valid serial number 192 at 3 77
Valid serial number 313 at 3 81
Valid serial number 31 at 3 92
Valid serial number 887 at 3 102
Valid serial number 234 at 3 120
Valid serial number 298 at 4 12
Valid serial number 922 at 4 20
Valid serial number 482 at 4 34
Valid serial number 395 at 4 97
Valid serial number 166 at 4 131
Valid ser

# Day 4

In [52]:
def parse_card(card_line: str) -> int:
    segments = line.rstrip("\n").split(": ")[1].split(" | ")
    winning_numbers, my_numbers = [set([int(a) for a in s.split(" ") if a]) for s in segments]
    matching_numbers = winning_numbers.intersection(my_numbers)
    return len(matching_numbers)

score = 0
with open("input_day_4") as f:
    for line in f:
        matches = parse_card(line)
        if matches:
            score += pow(2, matches-1)
        
        
print("Score", score)

Score 20829


In [53]:
num_scratchcards = 0
multipliers = []
with open("input_day_4") as f:
    for line in f:
        matches = parse_card(line)

        card_count = (multipliers.pop(0)+1) if multipliers else 1
        num_scratchcards += card_count

        # increase next matches elements in the queue by multiplier
        # append if nessesary
        for row_idx in range(matches):
            if row_idx < len(multipliers):
                multipliers[row_idx] += card_count
            else:
                multipliers.append(card_count)

        

assert len(multipliers) == 0, f"Queue should be empty {multipliers}"
print("Total number of scratchcards", num_scratchcards)

Total number of scratchcards 12648035


# Day 5

In [54]:
class ConversionDict():
    def __init__(self):
        self.mapping = dict()

    def add_conversion(self, dest: int, src: int, length: int):
        self.mapping[src] = (dest, length)

    def __getitem__(self, __key: Tuple[int,int]) -> List[Tuple[int,int]]:
        start, length = __key

        # if length == 1:
        if False:
            for src, (dest, conv_length) in self.mapping.items():
                if start >= src and start < src+conv_length:
                    return [(dest + (start-src), 1)]
            return [(start, 1)]
        else:
            resulting_ranges = []
            for src, (dest, conv_length) in sorted(self.mapping.items(), key=lambda t: t[0]):
                if start < src: 
                    # this conversion is after the start, so we can add the range up to the conversion
                    offset = min(length, src-start)
                    assert offset >= 0, f"Offset should be positive {offset}"
                    resulting_ranges.append((start, offset))
                    start += offset
                    length -= offset

                if length == 0:
                    return resulting_ranges
                    
                # add part of the conversion that is covered by the range
                if start >= src and start < src+conv_length:
                    offset_in_conv = min(start-src, conv_length)
                    assert offset_in_conv >= 0, f"Offset in conversion should be positive {offset_in_conv}"
                    assert offset_in_conv <= conv_length, f"Offset in conversion should be smaller than conversion length {offset_in_conv} < {conv_length}"
                    covered_length = min(length, conv_length-offset_in_conv)
                    assert covered_length >= 0, f"Covered length should be positive {covered_length}"
                    resulting_ranges.append((dest+offset_in_conv, covered_length))
                    start += covered_length
                    length -= covered_length

                    if length == 0:
                        return resulting_ranges
            assert length > 0, f"Length should be positive {length}"
            resulting_ranges.append((start, length))
            return resulting_ranges


def parse_map(map_string: str):
    components = map_string.split("\n")
    mappipng = components[0].split(" ")[0]
    src = mappipng.split("-")[0]
    dest = mappipng.split("-")[2]
    mapping = ConversionDict()

    for line in components[1:]:
        numbers = number_string_to_int_list(line)
        mapping.add_conversion(*numbers)
    return src, dest, mapping

with open("input_day_5_test1") as f:
    seeds = number_string_to_int_list(f.readline().rstrip("\n").split(": ")[1])
    seeds = [(s, 1) for s in seeds]
    print(seeds)
    _ = f.readline()
    maps = [parse_map(m) for m in f.read().split("\n\n")]
    print(maps)

for m in maps:
    new_seeds = []
    for s in seeds:
        new_seeds += m[2][s]
    seeds = new_seeds
print("Seeds after final conversion", seeds)
print("Min location", min(seeds)[0])

[(79, 1), (14, 1), (55, 1), (13, 1)]
[('seed', 'soil', <__main__.ConversionDict object at 0x7f9d2cd67590>), ('soil', 'fertilizer', <__main__.ConversionDict object at 0x7f9d2cd64210>), ('fertilizer', 'water', <__main__.ConversionDict object at 0x7f9d2cd641d0>), ('water', 'light', <__main__.ConversionDict object at 0x7f9d2cd65110>), ('light', 'temperature', <__main__.ConversionDict object at 0x7f9d2eff4450>), ('temperature', 'humidity', <__main__.ConversionDict object at 0x7f9d2eff6210>), ('humidity', 'location', <__main__.ConversionDict object at 0x7f9d2eff7dd0>)]
Seeds after final conversion [(82, 1), (43, 1), (86, 1), (35, 1)]
Min location 35


In [55]:
with open("input_day_5") as f:
    seeds = number_string_to_int_list(f.readline().rstrip("\n").split(": ")[1])
    # convert pair of seeds to (start, range_length)
    seeds = [(s, seeds[i+1]) for i,s in enumerate(seeds) if i%2 == 0]
    print(seeds)
    
    _ = f.readline()

    maps = [parse_map(m) for m in f.read().split("\n\n")]
    print(maps)

for m in maps:
    new_seeds = []
    for s in seeds:
        new_seeds += m[2][s]
    seeds = new_seeds
print("Seeds after final conversion", seeds)
print("Min location", min(seeds))

[(1482445116, 339187393), (3210489476, 511905836), (42566461, 51849137), (256584102, 379575844), (3040181568, 139966026), (4018529087, 116808249), (2887351536, 89515778), (669731009, 806888490), (2369242654, 489923931), (2086168596, 82891253)]
[('seed', 'soil', <__main__.ConversionDict object at 0x7f9d2cd63290>), ('soil', 'fertilizer', <__main__.ConversionDict object at 0x7f9d2cd63410>), ('fertilizer', 'water', <__main__.ConversionDict object at 0x7f9d2cd61390>), ('water', 'light', <__main__.ConversionDict object at 0x7f9d2cd61f10>), ('light', 'temperature', <__main__.ConversionDict object at 0x7f9d2cd62b50>), ('temperature', 'humidity', <__main__.ConversionDict object at 0x7f9d2cd61d10>), ('humidity', 'location', <__main__.ConversionDict object at 0x7f9d2cd60b50>)]
Seeds after final conversion [(3134759866, 20211188), (3154971054, 23987553), (718111107, 2523466), (3577569390, 6194161), (906358348, 15352358), (1009711192, 17989949), (47236480, 14645668), (3231718897, 1566255), (2239990

# Day 6

In [56]:
# parse input
# Time:      7  15   30
# Distance:  9  40  200

with open("input_day_6") as f:
    time = number_string_to_int_list(f.readline().rstrip("\n").split(": ")[1])
    distance = number_string_to_int_list(f.readline().rstrip("\n").split(": ")[1])

def compute_race_winning_posibilites(t: int, d: int) -> int:
    # solve: d < (t-p)*p
    # for p
    # p^2 - t*p + d < 0
    # solving for p
    # p = (t +- sqrt(t^2 - 4*d))/2
    p1 = (t + np.sqrt(t**2 - 4*d))/2
    p2 = (t - np.sqrt(t**2 - 4*d))/2
    x = math.ceil(p1) - math.floor(p2) -1
    print(p1,p2,x)
    # possible_durations = [p for p in range(1, t+1) if d < (t-p)*p]
    # x = len(possible_durations)
    return x
# compute possible duration of button presses to reach a higher distance for each race
product = 1
for t,d in zip(time,distance):
    product *= compute_race_winning_posibilites(t,d)
print("Possible durations product", product)
assert product == 633080

26.219544457292887 7.780455542707113 19
62.663521732655695 27.336478267344305 35
72.25337817275583 16.746621827244166 56
51.30662386291807 34.69337613708193 17
Possible durations product 633080


In [57]:
with open("input_day_6") as f:
    time = int(f.readline().rstrip("\n").split(": ")[1].replace(" ", ""))
    distance = int(f.readline().rstrip("\n").split(": ")[1].replace(" ", ""))

print("Time", time, "Distance", distance)
x = compute_race_winning_posibilites(time, distance)
print("Possible durations", x)
assert x == 20048741

Time 34908986 Distance 204171312101780
27478863.992000893 7430122.007999105 20048741
Possible durations 20048741


# Day 7

In [81]:
from collections import Counter
from functools import cmp_to_key, partial


def compare_hands(order: List[str], joker: bool, hand1: str, hand2: str) -> int:
    
    print("Hands", hand1, hand2)
    # compare by rules
    g1 = Counter(hand1)
    g2 = Counter(hand2)
    print("Counters", g1, g2)

    # five of a kind 1
    # four of a kind 2
    # full house 2
    # three of a kind 3
    # two pairs 3
    # one pair 4

    if joker:
        if "J" in g1 and len(g1) > 1:
            j_count = g1["J"]
            del g1["J"]
            g1[max(g1, key=g1.get)] += j_count
        if "J" in g2 and len(g2) > 1:
            j_count = g2["J"]
            del g2["J"]
            g2[max(g2, key=g2.get)] += j_count

    assert sum(g1.values()) == 5, f"Hand 1 {hand1} should have 5 cards {g1}"
    assert sum(g2.values()) == 5, f"Hand 2 {hand2} should have 5 cards {g2}"

    if len(g1) < len(g2):
        print("Hand 1 wins")
        return 1
    elif len(g1) > len(g2):
        print("Hand 2 wins")
        return -1

    if len(g1) == len(g2) == 2:
        # four of a kind
        if 4 in g1.values() and 4 not in g2.values():
            print("Hand 1 wins")
            return 1
        elif 4 in g2.values() and 4 not in g1.values():
            print("Hand 2 wins")
            return -1
        # full house, proceed with by card comparision
        
    elif len(g1) == len(g2) == 3:
        # three of a kind
        if 3 in g1.values() and 3 not in g2.values():
            print("Hand 1 wins")
            return 1
        elif 3 in g2.values() and 3 not in g1.values():
            print("Hand 2 wins")
            return -1
        # two pairs, proceed with by card comparision
        
    # compare by character
    for c1,c2 in zip(hand1, hand2):
        if c1 != c2:
            i1 = order.index(c1)
            i2 = order.index(c2)
            assert i1 >= 0 and i2 >= 0, f"Character not in order {c1} {c2}"
            print("Hand", 1 if i1 < i2 else 2, "wins by card comparison")
            return 1 if i1 < i2 else -1
        
    assert False, "All cards should be different"
    return 0


with open("input_day_7") as f:
    lines = f.readlines()
    hands_with_bid = [l.rstrip("\n").split(" ") for l in lines]
    # print(hands_with_bid)

# sort hands 
order = ["A", "K", "Q", "J", "T", "9", "8", "7", "6", "5", "4", "3", "2"]
hands_with_bid = sorted(hands_with_bid, key=lambda x: cmp_to_key(partial(compare_hands, order, False))(x[0]))
# print(hands_with_bid)
# assert "QQQJA" == hands_with_bid[4][0], f"Expected QQQJA, got {hands_with_bid[4][0]}"
# assert "T55J5" == hands_with_bid[3][0], f"Expected T55J5, got {hands_with_bid[3][0]}"
# assert "KK677" == hands_with_bid[2][0], f"Expected KK677, got {hands_with_bid[2][0]}"
# assert "KTJJT" == hands_with_bid[1][0], f"Expected KTJJT, got {hands_with_bid[1][0]}"
# assert "32T3K" == hands_with_bid[0][0], f"Expected 32T3K, got {hands_with_bid[0][0]}"

bid_rank_product = 0
for row_idx, (hand, bid) in enumerate(hands_with_bid):
    # print(f"Hand {i+1} with bid {bid} has hand {hand}")
    bid_rank_product += (row_idx+1)*int(bid)
print("Bid rank product", bid_rank_product)

Hands Q33J3 A833A
Counters Counter({'3': 3, 'Q': 1, 'J': 1}) Counter({'A': 2, '3': 2, '8': 1})
Hand 1 wins
Hands 55KK5 Q33J3
Counters Counter({'5': 3, 'K': 2}) Counter({'3': 3, 'Q': 1, 'J': 1})
Hand 1 wins
Hands K4457 55KK5
Counters Counter({'4': 2, 'K': 1, '5': 1, '7': 1}) Counter({'5': 3, 'K': 2})
Hand 2 wins
Hands K4457 Q33J3
Counters Counter({'4': 2, 'K': 1, '5': 1, '7': 1}) Counter({'3': 3, 'Q': 1, 'J': 1})
Hand 2 wins
Hands K4457 A833A
Counters Counter({'4': 2, 'K': 1, '5': 1, '7': 1}) Counter({'A': 2, '3': 2, '8': 1})
Hand 2 wins
Hands Q3QT3 Q33J3
Counters Counter({'Q': 2, '3': 2, 'T': 1}) Counter({'3': 3, 'Q': 1, 'J': 1})
Hand 2 wins
Hands Q3QT3 A833A
Counters Counter({'Q': 2, '3': 2, 'T': 1}) Counter({'A': 2, '3': 2, '8': 1})
Hand 2 wins by card comparison
Hands Q3QT3 K4457
Counters Counter({'Q': 2, '3': 2, 'T': 1}) Counter({'4': 2, 'K': 1, '5': 1, '7': 1})
Hand 1 wins
Hands QJK32 A833A
Counters Counter({'Q': 1, 'J': 1, 'K': 1, '3': 1, '2': 1}) Counter({'A': 2, '3': 2, '8': 1}

In [83]:
with open("input_day_7") as f:
    lines = f.readlines()
    hands_with_bid = [l.rstrip("\n").split(" ") for l in lines]
    # print(hands_with_bid)


# sort hands 
order = ["A", "K", "Q", "T", "9", "8", "7", "6", "5", "4", "3", "2", "J"]

two_pair = "23J5J"
three_of_a_kind = "JAAKA"
compare_hands(order, True, two_pair, three_of_a_kind)
hands_with_bid = sorted(hands_with_bid, key=lambda x: cmp_to_key(partial(compare_hands, order, True))(x[0]))
print(hands_with_bid)
# assert "AAAAJ" == hands_with_bid[6][0], f"Expected AAAAJ, got {hands_with_bid[6][0]}"
# assert "JJJJJ" == hands_with_bid[5][0], f"Expected JJJJJ, got {hands_with_bid[5][0]}"
# assert "KTJJT" == hands_with_bid[4][0], f"Expected KTJJT, got {hands_with_bid[4][0]}"
# assert "QQQJA" == hands_with_bid[3][0], f"Expected QQQJA, got {hands_with_bid[3][0]}"
# assert "T55J5" == hands_with_bid[2][0], f"Expected T55J5, got {hands_with_bid[2][0]}"
# assert "KK677" == hands_with_bid[1][0], f"Expected KK677, got {hands_with_bid[1][0]}"
# assert "32T3K" == hands_with_bid[0][0], f"Expected 32T3K, got {hands_with_bid[0][0]}"

bid_rank_product = 0
for row_idx, (hand, bid) in enumerate(hands_with_bid):
    print(f"Hand {row_idx+1} with bid {bid} has hand {hand}")
    bid_rank_product += (row_idx+1)*int(bid)
print("Bid rank product", bid_rank_product)

Hands 23J5J JAAKA
Counters Counter({'J': 2, '2': 1, '3': 1, '5': 1}) Counter({'A': 3, 'J': 1, 'K': 1})
Hand 2 wins
Hands Q33J3 A833A
Counters Counter({'3': 3, 'Q': 1, 'J': 1}) Counter({'A': 2, '3': 2, '8': 1})
Hand 1 wins
Hands 55KK5 Q33J3
Counters Counter({'5': 3, 'K': 2}) Counter({'3': 3, 'Q': 1, 'J': 1})
Hand 2 wins
Hands 55KK5 Q33J3
Counters Counter({'5': 3, 'K': 2}) Counter({'3': 3, 'Q': 1, 'J': 1})
Hand 2 wins
Hands 55KK5 A833A
Counters Counter({'5': 3, 'K': 2}) Counter({'A': 2, '3': 2, '8': 1})
Hand 1 wins
Hands K4457 55KK5
Counters Counter({'4': 2, 'K': 1, '5': 1, '7': 1}) Counter({'5': 3, 'K': 2})
Hand 2 wins
Hands K4457 A833A
Counters Counter({'4': 2, 'K': 1, '5': 1, '7': 1}) Counter({'A': 2, '3': 2, '8': 1})
Hand 2 wins
Hands Q3QT3 55KK5
Counters Counter({'Q': 2, '3': 2, 'T': 1}) Counter({'5': 3, 'K': 2})
Hand 2 wins
Hands Q3QT3 A833A
Counters Counter({'Q': 2, '3': 2, 'T': 1}) Counter({'A': 2, '3': 2, '8': 1})
Hand 2 wins by card comparison
Hands Q3QT3 K4457
Counters Counter

# Day 8

In [14]:
with open("input_day_8") as f:
    sequence = f.readline().rstrip("\n")
    print(sequence)
    f.readline()
    mappings = {l.split(" = ")[0]: l.split(" = ")[1][1:-1].split(", ") for l in f.read().split("\n")}
    print(mappings)

steps = 0
position = "AAA"
while position != "ZZZ":
    direction = sequence[steps % len(sequence)]
    direction_index = 0 if direction == "L" else 1
    position = mappings[position][direction_index]
    steps += 1
print("Steps", steps)

LLRLLRRLRLRRRLRRLLRRRLRLRLRRLRRRLRRLRLRLLRLLLRRRLRRLRRRLRRRLRRRLRLRRLLRRLRRLRRLRRRLRLRRRLLRLRRLRRRLRLRRRLRRRLRLRRRLLRRRLRRRLRLRRLRLRRRLLRRLRRLRRLRRLRLRLRRRLLRRRLRRLRRRLRLRLRRRLLRLRRLLRLRRLRLRRRLRLRRLLRRRLLRRLRLRLLRLLRRLRRLLRRLRLRRLRLRLRRRLRRLRLLLLRRLRLRLRRRLLLRRRLRRLRRLRLLRLRRRLLLRRRLRRRLRRRR
{'NQT': ['TXC', 'RVJ'], 'FPT': ['PNS', 'KJL'], 'BNQ': ['THG', 'LCV'], 'SPL': ['VBH', 'NNV'], 'TLM': ['LVQ', 'PGT'], 'GHC': ['XKN', 'SPR'], 'PHT': ['HMF', 'DST'], 'FSF': ['JCM', 'SMT'], 'GDD': ['FHJ', 'RBS'], 'GVR': ['FVD', 'FVD'], 'SST': ['PMF', 'MGC'], 'ZZZ': ['VLV', 'SQV'], 'SDV': ['DBL', 'GTL'], 'XSP': ['GRV', 'RFM'], 'SKG': ['NGH', 'VDX'], 'BPK': ['RMK', 'LCQ'], 'VSC': ['DRN', 'SFR'], 'BFR': ['BJR', 'GMD'], 'HTM': ['PFM', 'LVD'], 'XVP': ['LDP', 'LDP'], 'DRD': ['SCH', 'LKD'], 'DSJ': ['GSQ', 'JTN'], 'VTS': ['BNQ', 'VFX'], 'KVF': ['HTP', 'MQK'], 'GPS': ['FXQ', 'TPF'], 'VRC': ['RTK', 'RTK'], 'HRD': ['PMQ', 'JCR'], 'DJK': ['FTC', 'KXH'], 'VGJ': ['PCJ', 'TVH'], 'QMN': ['TLC', 'HNG'], 'DMH': ['QSD', 

In [25]:
with open("input_day_8_part2") as f:
    sequence = f.readline().rstrip("\n")
    print(sequence)
    f.readline()
    mappings = {l.split(" = ")[0]: l.split(" = ")[1][1:-1].split(", ") for l in f.read().split("\n")}
    print("Total number of mappings", len(mappings))

steps = 0
positions = [k for k in mappings.keys() if k.endswith("A")]
print("Number of simultaneous positions", len(positions))
z_node_seen_at = [defaultdict(list) for _ in range(len(positions))]

periodicity_steps = [None for _ in range(len(positions))]

while not all(p.endswith("Z") for p in positions):
    direction = sequence[steps % len(sequence)]
    direction_index = 0 if direction == "L" else 1

    positions = [mappings[p][direction_index] for p in positions]
    steps += 1


    for row_idx,p in enumerate(positions):
        if p.endswith("Z"):
            z_node_seen_at[row_idx][p].append(steps)
            assert len(z_node_seen_at[row_idx]) <= 1, f"Multiple Z nodes seen at {p} for position {row_idx}"

            if len(z_node_seen_at[row_idx][p]) == 3:
                p_0_1 = z_node_seen_at[row_idx][p][1] - z_node_seen_at[row_idx][p][0]
                p_1_2 = z_node_seen_at[row_idx][p][2] - z_node_seen_at[row_idx][p][1]
                p_0 = z_node_seen_at[row_idx][p][0]
                print("Periodicity for position", row_idx, "is", p_0_1, p_1_2, p_0)
                assert p_0 == p_0_1, f"Periodicity should be the same {p_0} {p_0_1}"
                assert p_0_1 == p_1_2, f"Periodicity should be the same {p_0_1} {p_1_2}"
                periodicity_steps[row_idx] = p_0_1
    
    if all(p for p in periodicity_steps):
        print("Found all periodicity steps", periodicity_steps)
        break

# compute lcm of periodicity steps using numpy
periodicity_steps = np.array(periodicity_steps)
lcm = np.lcm.reduce(periodicity_steps)
print("LCM", lcm)
print("Steps", steps)

LLRLLRRLRLRRRLRRLLRRRLRLRLRRLRRRLRRLRLRLLRLLLRRRLRRLRRRLRRRLRRRLRLRRLLRRLRRLRRLRRRLRLRRRLLRLRRLRRRLRLRRRLRRRLRLRRRLLRRRLRRRLRLRRLRLRRRLLRRLRRLRRLRRLRLRLRRRLLRRRLRRLRRRLRLRLRRRLLRLRRLLRLRRLRLRRRLRLRRLLRRRLLRRLRLRLLRLLRRLRRLLRRLRLRRLRLRLRRRLRRLRLLLLRRLRLRLRRRLLLRRRLRRLRRLRLLRLRRRLLLRRRLRRRLRRRR
Total number of mappings 738
Number of simultaneous positions 6
Periodicity for position 2 is 12599 12599 12599
Periodicity for position 4 is 13771 13771 13771
Periodicity for position 1 is 17287 17287 17287
Periodicity for position 0 is 19631 19631 19631
Periodicity for position 5 is 20803 20803 20803
Periodicity for position 3 is 23147 23147 23147
Found all periodicity steps [19631, 17287, 12599, 23147, 13771, 20803]
LCM 13129439557681
Steps 69441


# Day 9

In [18]:
def compute_pairwise_differences(numbers: List[int]) -> List[int]:
    return [numbers[i+1] - numbers[i] for i in range(len(numbers)-1)]

def compute_next_sequence_element(numbers: List[int]) -> int:

    if all(0 == d for d in numbers):
        next_num = 0
    else:
        differences = compute_pairwise_differences(numbers)
        next_difference = compute_next_sequence_element(differences)
        next_num = differences[-1] + next_difference
    return next_num

with open("input_day_9") as f:
    sequences = [number_string_to_int_list(l.rstrip("\n")) for l in f.readlines()]
    
total_sum = 0
for seq in sequences:
    next_seq = compute_next_sequence_element(seq)
    next_num = seq[-1] + next_seq
    total_sum += next_num

print("Total sum", total_sum)

Total sum 1684566095


In [21]:
# backwards
with open("input_day_9") as f:
    sequences = [number_string_to_int_list(l.rstrip("\n")) for l in f.readlines()]

total_sum = 0
for seq in sequences:
    seq = seq[::-1]
    next_seq = compute_next_sequence_element(seq)
    next_num = seq[-1] + next_seq
    total_sum += next_num

print("Total sum", total_sum)

Total sum 1136


# Day 10

In [57]:
# | is a vertical pipe connecting north and south.
# - is a horizontal pipe connecting east and west.
# L is a 90-degree bend connecting north and east.
# J is a 90-degree bend connecting north and west.
# 7 is a 90-degree bend connecting south and west.
# F is a 90-degree bend connecting south and east.
# . is ground; there is no pipe in this tile.

# (0,0) is the top left corner (Y,X)
connections = {
    "|": [(-1,0), (1,0)], # north, south
    "-": [(0,1), (0,-1)], # east, west
    "L": [(-1,0), (0,1)], # north, east
    "J": [(-1,0), (0,-1)], # north, west 
    "7": [(1,0), (0,-1)], # south, west
    "F": [(1,0), (0,1)], # south, east
    ".": []
}

with open("input_day_10") as f:
    # read as 2D array of characters
    grid = [list(l.rstrip("\n")) for l in f.readlines()]

def find_start(grid: List[List[str]]) -> Tuple[int,int]:
    # find coordinates of "S"
    start = None
    for i,row in enumerate(grid):
        for j,c in enumerate(row):
            if c == "S":
                start = (i,j)
                break
        if start:
            break
    assert start, "Start should be found"
    print("Start", start)
    return start

def find_neighbours_of_start(grid: List[List[str]], start: Tuple[int,int]) -> Tuple[Tuple[Tuple[int,int], Tuple[int,int]], str]:
    # find neighbours that connect to start
    neighbours = []
    inverse_dirs = set()
    for c,dirs in connections.items():
        for dir in dirs:
            # add start with inverse direction
            inverse_dir = (-dir[0], -dir[1])
            target = (start[0] + inverse_dir[0], start[1] + inverse_dir[1])
            if target[0] >= 0 and target[0] < len(grid) and target[1] >= 0 and target[1] < len(grid[0]):
                if grid[target[0]][target[1]] == c:
                    print("Found neighbour", c, "at position", target)
                    neighbours.append(target)
                    assert start == (target[0] + dir[0], target[1] + dir[1]), f"Start should be inverse direction of neighbour {start} {target} {dir}"
                    inverse_dirs.add(inverse_dir)
    assert len(neighbours) == 2, f"Should have 2 neighbours {neighbours}"

    start_tile_type: str = [c for c,cdirs in connections.items() if set(cdirs) == inverse_dirs][0]
    return neighbours, start_tile_type
    

def compute_distances(grid: List[List[str]]) -> List[List[int|None]]:
    start = find_start(grid)

    distances = [[None for _ in range(len(grid[0]))] for _ in range(len(grid))]
    distances[start[0]][start[1]] = 0

    
    neighbours, _ = find_neighbours_of_start(grid, start)
    distance = 1
    print("Neighbours", neighbours)
    current_positions = neighbours

    while current_positions:
        for pos in current_positions:
            distances[pos[0]][pos[1]] = distance

        new_neighbours = []
        for pos in current_positions:
            pipe_type = grid[pos[0]][pos[1]]
            dirs = connections[pipe_type]
            for dir in dirs:
                target = (pos[0] + dir[0], pos[1] + dir[1])
                if target[0] >= 0 and target[0] < len(grid) and target[1] >= 0 and target[1] < len(grid[0]):
                    if grid[target[0]][target[1]] != ".":
                        if distances[target[0]][target[1]] is None:
                            print(pos, "Found neighbour", grid[target[0]][target[1]], "at position", target)
                            distances[target[0]][target[1]] = distance
                            new_neighbours.append(target)
        print("New neighbours", new_neighbours)
        current_positions = new_neighbours
        distance += 1
    return distances

distances = compute_distances(grid)
print("Distances", distances)
print("Maximum distance", max([d for row in distances for d in row if d is not None]))

Start (94, 98)
Found neighbour - at position (94, 99)
Found neighbour L at position (94, 97)
Neighbours [(94, 99), (94, 97)]
(94, 99) Found neighbour - at position (94, 100)
(94, 97) Found neighbour F at position (93, 97)
New neighbours [(94, 100), (93, 97)]
(94, 100) Found neighbour - at position (94, 101)
(93, 97) Found neighbour - at position (93, 98)
New neighbours [(94, 101), (93, 98)]
(94, 101) Found neighbour - at position (94, 102)
(93, 98) Found neighbour - at position (93, 99)
New neighbours [(94, 102), (93, 99)]
(94, 102) Found neighbour - at position (94, 103)
(93, 99) Found neighbour - at position (93, 100)
New neighbours [(94, 103), (93, 100)]
(94, 103) Found neighbour - at position (94, 104)
(93, 100) Found neighbour J at position (93, 101)
New neighbours [(94, 104), (93, 101)]
(94, 104) Found neighbour - at position (94, 105)
(93, 101) Found neighbour | at position (92, 101)
New neighbours [(94, 105), (92, 101)]
(94, 105) Found neighbour - at position (94, 106)
(92, 101

In [35]:
import sys
print(sys.getrecursionlimit())

3000


In [39]:
sys.setrecursionlimit(int(10e7))

In [62]:
with open("input_day_10") as f:
    # read as 2D array of characters
    grid = [list(l.rstrip("\n")) for l in f.readlines()]




distances = compute_distances(grid)
print("Distances", distances)
print("Maximum distance", max([d for row in distances for d in row if d is not None]))




loop_grid = [[c if distances[i][j] is not None else "." for j,c in enumerate(row)] for i,row in enumerate(grid)]

start = find_start(loop_grid)
_, start_tile_type = find_neighbours_of_start(loop_grid, start)
print("Start tile type", start_tile_type)

# replace "S" with the correct connection type
loop_grid[start[0]][start[1]] = start_tile_type





# scale up by factor 3, respecing the connection type
connections_scaled_up = {
    "|": [[0,1,0], [0,1,0], [0,1,0]], # north, south
    "-": [[0,0,0], [1,1,1], [0,0,0]], # east, west
    "L": [[0,1,0], [0,1,1], [0,0,0]], # north, east
    "J": [[0,1,0], [1,1,0], [0,0,0]], # north, west
    "7": [[0,0,0], [1,1,0], [0,1,0]], # south, west
    "F": [[0,0,0], [0,1,1], [0,1,0]], # south, east
    ".": [[0,0,0], [0,0,0], [0,0,0]]
}
loop = np.zeros((len(loop_grid)*3, len(loop_grid[0])*3), dtype=int)
for row_idx,row in enumerate(loop_grid):
    for j,c in enumerate(row):
        loop[3*row_idx:3*row_idx+3, 3*j:3*j+3] = connections_scaled_up[c]
    
print("Loop", loop)

# save loop to a file
np.savetxt("loop_scaled_up.txt", loop, fmt="%d", delimiter="")





# flood fill from outside point
def flood_fill(grid: np.ndarray, point: Tuple[int,int], fill_value: int, target_value: int) -> None:
    if grid[point[0], point[1]] == target_value:
        grid[point[0], point[1]] = fill_value
        for dir in [(0,1), (0,-1), (1,0), (-1,0)]:
            new_point = (point[0] + dir[0], point[1] + dir[1])
            if new_point[0] >= 0 and new_point[0] < grid.shape[0] and new_point[1] >= 0 and new_point[1] < grid.shape[1]:
                flood_fill(grid, new_point, fill_value, target_value)

outside_points = [(0,j) for j in range(loop.shape[1])] + [(loop.shape[0]-1, j) for j in range(loop.shape[1])] + [(i,0) for i in range(loop.shape[0])] + [(i,loop.shape[1]-1) for i in range(loop.shape[0])]
for outside_point in outside_points:
    flood_fill(loop, outside_point, 2, 0)
print("Loop", loop)

# save flood filled loop to a file
np.savetxt("loop_flood_filled.txt", loop, fmt="%d", delimiter="")

# scale down by factor 3 taking the middle of each 3x3 block
loop_scaled_down = np.zeros((int(loop.shape[0]/3), int(loop.shape[1]/3)), dtype=int)
for row_idx in range(loop_scaled_down.shape[0]):
    for j in range(loop_scaled_down.shape[1]):
        loop_scaled_down[row_idx,j] = loop[3*row_idx+1][3*j+1]
loop = loop_scaled_down

# save scaled down loop to a file
np.savetxt("loop_scaled_down.txt", loop, fmt="%d", delimiter="")

# count number of 0s in loop
enclosed_size = int(np.sum(loop == 0))
print("Enclosed size", enclosed_size)


Start (94, 98)
Found neighbour - at position (94, 99)
Found neighbour L at position (94, 97)
Neighbours [(94, 99), (94, 97)]
(94, 99) Found neighbour - at position (94, 100)
(94, 97) Found neighbour F at position (93, 97)
New neighbours [(94, 100), (93, 97)]
(94, 100) Found neighbour - at position (94, 101)
(93, 97) Found neighbour - at position (93, 98)
New neighbours [(94, 101), (93, 98)]
(94, 101) Found neighbour - at position (94, 102)
(93, 98) Found neighbour - at position (93, 99)
New neighbours [(94, 102), (93, 99)]
(94, 102) Found neighbour - at position (94, 103)
(93, 99) Found neighbour - at position (93, 100)
New neighbours [(94, 103), (93, 100)]
(94, 103) Found neighbour - at position (94, 104)
(93, 100) Found neighbour J at position (93, 101)
New neighbours [(94, 104), (93, 101)]
(94, 104) Found neighbour - at position (94, 105)
(93, 101) Found neighbour | at position (92, 101)
New neighbours [(94, 105), (92, 101)]
(94, 105) Found neighbour - at position (94, 106)
(92, 101

# Day 11

In [36]:
with open("input_day_11_test1") as f:
    grid = [list(l.rstrip("\n")) for l in f.readlines()]


def expand_galaxy(grid: List[List[str]], factor=2) -> List[List[str]]:
    # double any rows that contain just "."
    grid = [[row]*factor if all(c == "." for c in row) else [row] for row in grid]
    grid = list(itertools.chain(*grid))
    # double any columns that contain just "."
    grid = [list(col) for col in zip(*grid)]
    grid = [[col]*factor if all(c == "." for c in col) else [col] for col in grid]
    grid = list(itertools.chain(*grid))
    # transpose back
    grid = [list(col) for col in zip(*grid)]
    return grid

def compute_sum_of_distances(galaxy_coords: List[Tuple[int,int]]) -> int:
    # compute pairs of coordinates
    galaxy_pairs = list(itertools.combinations(galaxy_coords, 2))

    # compute distance between pairs
    galaxy_distances = [np.linalg.norm(np.array(p[0]) - np.array(p[1]), ord=1) for p in galaxy_pairs]

    # compute sum of distances
    galaxy_sum = int(np.sum(galaxy_distances))
    return galaxy_sum

grid = expand_galaxy(grid, 2)
grid = np.array(grid)

# list of coordinates of "#" in grid
galaxy_coords = list(zip(*np.where(grid == "#")))
galaxy_sum = compute_sum_of_distances(galaxy_coords)
print("Sum of distances between galaxies", galaxy_sum)

Sum of distances between galaxies 374


In [34]:
with open("input_day_11") as f:
    grid = [list(l.rstrip("\n")) for l in f.readlines()]

grid = np.array(grid)

# list of coordinates of "#" in grid
galaxy_coords = list(zip(*np.where(grid == "#")))

# rows/cols with galaxies computed from galaxy_coords
galaxy_rows = set([c[0] for c in galaxy_coords])
galaxy_cols = set([c[1] for c in galaxy_coords])

# compute rows/cols with no galaxies
empty_rows = set(range(grid.shape[0])) - galaxy_rows
empty_cols = set(range(grid.shape[1])) - galaxy_cols

galaxy_coords = np.array(galaxy_coords)

print("Galaxy Coords shape", galaxy_coords.shape)
print("Number of empty rows", len(empty_rows))
print("Number of empty cols", len(empty_cols))

factor = 1000000 - 1 # subtract one for the existing empty row/col
expansion = np.zeros_like(galaxy_coords)
# increase every coordinate by factor for each empty row/col before it
for r in empty_rows:
    expansion[:,0] = np.where(galaxy_coords[:,0] > r, expansion[:,0]+factor, expansion[:,0])
for c in empty_cols:
    expansion[:,1] = np.where(galaxy_coords[:,1] > c, expansion[:,1]+factor, expansion[:,1])

galaxy_coords += expansion
galaxy_sum = compute_sum_of_distances(galaxy_coords)
print("Sum of distances between galaxies", galaxy_sum)

Galaxy Coords shape (443, 2)
Number of empty rows 6
Number of empty cols 4
Sum of distances between galaxies 377318892554


# Day 12

# Day 13

In [60]:
def find_reflection_row_index(grid: np.ndarray, num_exact_faults=0) -> int | None:
    for row_idx in range(grid.shape[0]-1):
        reflected_part_length = min(row_idx+1, grid.shape[0] - row_idx -1)

        upper_grid = grid[row_idx+1-reflected_part_length:row_idx+1]
        lower_grid = grid[row_idx+1:row_idx+1+reflected_part_length]

        assert lower_grid.shape == upper_grid.shape,  (grid.shape, row_idx, reflected_part_length, lower_grid.shape, upper_grid.shape)

        # reflect the lower grid horizontally
        lower_grid = np.flip(lower_grid, 0)

        inequality = ~(lower_grid == upper_grid)
        if np.sum(inequality.astype(int)) == num_exact_faults:
            return row_idx

    return None


def day_13_part_1(filename, find_reflection_func = find_reflection_row_index) -> int:
    with open(filename) as f:
        grids = f.read().split("\n\n")
        grids = [[list(l.rstrip("\n")) for l in gf.split("\n")] for gf in grids]
    
    result = 0
    for grid in grids:
        grid = np.array(grid)
        idx = find_reflection_func(grid)
        if idx is not None:
            result += (idx+1) * 100
            continue
        
        # seach for reflection column
        grid_transposed = np.transpose(grid)
        idx = find_reflection_func(grid_transposed)

        grid_str = ('\n'.join(''.join(map(str, row)) for row in grid))
        assert idx is not None, f"Did not find reflection for grid\n{grid_str}"
        result += (idx+1)
    return result

assert day_13_part_1("input_day_13_test1") == 405, day_13_part_1("input_day_13_test1")
assert day_13_part_1("input_day_13_test2") == 100


print("Solution day 13 part 1", day_13_part_1("input_day_13"))

Solution day 13 part 1 30518


In [62]:
def day_13_part_2(filename: str):
    return day_13_part_1(filename, find_reflection_func=lambda x: find_reflection_row_index(x, num_exact_faults=1))

assert day_13_part_2("input_day_13_test1") == 400, day_13_part_2("input_day_13_test1")

print("Solution day 13 part 2", day_13_part_2("input_day_13"))

Solution day 13 part 2 36735


# Day 14

In [2]:
def shift_row(row: List[str]) -> List[str]:
    shifted_row = []
    for c in row:
        if c == "O":
            # find index where "O" goes
            # find the last index of "#" or "O" or 0
            end_index = -1
            for i in range(len(shifted_row)-1, -1, -1):
                if shifted_row[i] == "#" or shifted_row[i] == "O":
                    end_index = i
                    break
            if end_index == -1:
                # no "#" or "O" found, insert on the left
                shifted_row.insert(0, "O")
            else:
                # insert on the right of end_index
                shifted_row.insert(end_index+1, "O")


        elif c == "#":
            shifted_row.append("#")
        elif c == ".":
            shifted_row.append(".")
    assert len(row) == len(shifted_row), f"Row should have same length {len(row)} {len(shifted_row)}"
    return shifted_row

assert shift_row(".O") == ['O', '.']
assert shift_row(".O#..O.#.#O") == ['O', '.', '#', 'O', '.', '.', '.', '#', '.', '#', 'O']



with open("input_day_14") as f:
    grid = [list(l.rstrip("\n")) for l in f.readlines()]


def tilt_north(grid: List[List[str]]) -> List[List[str]]:
    # transpose the grid
    grid = [list(col) for col in zip(*grid)]

    grid = [shift_row(row) for row in grid]

    # transpose the grid back
    grid = [list(col) for col in zip(*grid)]
    return grid

grid = tilt_north(grid)

# weight row by revese index, e.g. last row is weighted 1, second to last is weighted 2, etc.
# multiply each weight by the number of "O"s in the row
# sum all weights
total_sum = 0
for row_idx,row in enumerate(grid[::-1]):
    total_sum += (row_idx+1)*row.count("O")
print("Total sum", total_sum)

Total sum 105249


In [8]:
with open("input_day_14") as f:
    grid = [list(l.rstrip("\n")) for l in f.readlines()]


def cycle_of_tilts(grid: List[List[str]]) -> List[List[str]]:
    grid = tilt_north(grid)

    # rotate grid 90 degress counter clockwise
    grid = [list(col) for col in zip(*grid[::-1])]
    grid = tilt_north(grid)

    # rotate grid 90 degress counter clockwise
    grid = [list(col) for col in zip(*grid[::-1])]
    grid = tilt_north(grid)

    # rotate grid 90 degress counter clockwise
    grid = [list(col) for col in zip(*grid[::-1])]
    grid = tilt_north(grid)

    # rotate grid 90 degress counter clockwise
    grid = [list(col) for col in zip(*grid[::-1])]

    return grid


seen_hashes = {}
periodicity = None
offset = None
cycles = 1000000000
for row_idx in tqdm(range(cycles)):
    new_grid = cycle_of_tilts(grid)


    new_grid_hash = hash(tuple([tuple(row) for row in new_grid])) 
    if new_grid_hash in seen_hashes:
        print("Cycle", row_idx, "saw grid hash before", new_grid_hash, "at cycle", seen_hashes[new_grid_hash])
        periodicity = row_idx - seen_hashes[new_grid_hash]
        offset = row_idx
        print("Periodicity", periodicity)
        break
    else:
        seen_hashes[new_grid_hash] = row_idx

    grid = new_grid

assert periodicity is not None, "Periodicity should be found"
assert offset is not None, "Offset should be found"

# compute the grid at the end of the cycles
cycles_left = cycles - offset
cycles_left %= periodicity
print("Cycles left", cycles_left)
for row_idx in range(cycles_left):
    grid = cycle_of_tilts(grid)

# save the grid to a file without spaces between the characters. use numpy
np.savetxt("input_day_14_tilted.txt", np.array(grid), fmt="%s", delimiter="")


# weight row by revese index, e.g. last row is weighted 1, second to last is weighted 2, etc.
# multiply each weight by the number of "O"s in the row
# sum all weights
total_sum = 0
for row_idx,row in enumerate(grid[::-1]):
    total_sum += (row_idx+1)*row.count("O")
print("Total sum", total_sum)

  0%|          | 149/1000000000 [00:01<2336:20:07, 118.89it/s]


Cycle 149 saw grid hash before -6057235955602063980 at cycle 107
Periodicity 42
Cycles left 11
Total sum 88680


# Day 15

In [19]:
def aoc_hash(instruction: str) -> int:
    counter = 0
    for c in instruction:
        counter += ord(c)
        counter *= 17
        counter %= 256
    return counter

def day_15_part_1(initialization_sequence: str) -> int:
    return sum([aoc_hash(instr) for instr in initialization_sequence.split(",")])

assert day_15_part_1("rn=1,cm-,qp=3,cm=2,qp-,pc=4,ot=9,ab=5,pc-,pc=6,ot=7") == 1320


with open("input_day_15") as f:
    initialization_sequence = f.readline().rstrip("\n")
print("Day 15 part 1 solution", day_15_part_1(initialization_sequence))

Day 15 part 1 solution 522547


In [56]:
def compute_final_boxes(initialization_sequence:str) -> List[List[Tuple[str,int]]]:
    boxes = [[] for i in range(256)]
    for instr in initialization_sequence.split(","):
        # split instr "rn=1" into parts
        if "=" in instr:
            label, lens = instr.split("=")
            box_id = aoc_hash(label)
            
            idx = -1
            for i, (l,f) in enumerate(boxes[box_id]):
                if l == label:
                    idx = i
                    break
            if idx == -1:
                boxes[box_id].append((label, int(lens)))
            else:
                boxes[box_id][idx] = (label, int(lens))
        elif instr.endswith("-"):
            label = instr[:-1]
            box_id = aoc_hash(label)
            boxes[box_id] = [(l,f) for (l,f) in boxes[box_id] if l != label]
    return boxes

test = compute_final_boxes("rn=1,cm-,qp=3,cm=2,qp-,pc=4,ot=9,ab=5,pc-,pc=6,ot=7")
print(test)
assert test[0] == [("rn", 1), ("cm", 2)]
assert test[3] == [("ot", 7), ("ab", 5), ("pc", 6)]


def day_15_part_2(initialization_sequence:str) -> int:
    boxes = compute_final_boxes(initialization_sequence)

    total_focusing_power = sum([(box_idx+1)*(lens_idx+1)*f for box_idx,box in enumerate(boxes) for lens_idx,(l,f) in enumerate(box)])
    return total_focusing_power

assert day_15_part_2("rn=1,cm-,qp=3,cm=2,qp-,pc=4,ot=9,ab=5,pc-,pc=6,ot=7") == 145

with open("input_day_15") as f:
    initialization_sequence = f.readline().rstrip("\n")
print("Day 15 part 2 solution", day_15_part_2(initialization_sequence))

[[('rn', 1), ('cm', 2)], [], [], [('ot', 7), ('ab', 5), ('pc', 6)], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], 

# Day 17

In [48]:

def day_17_part_1(filename: str):
    with open(filename) as f:
        grid = np.array([list(l.rstrip("\n")) for l in f.readlines()], dtype=int)

    shortest = [[{} for _ in range(grid.shape[1])] for _ in range(grid.shape[0])]
    queue = [ # ((y,x), heat_loss, directions (rldu))
        (np.array((0,1)), grid[0][1], "r"),
        (np.array((1,0)), grid[1][0], "d")
    ]

    while queue:
        pos, heat_loss, path = queue.pop(0)

        directions = {"r": np.array((0,1)), "l": np.array((0,-1)), "d": np.array((1,0)), "u": np.array((-1,0))}

        new_queue_elements = []
        for direction, offset in directions.items():
            target = pos + offset
            last_directions = path[-3:]
            if 0 <= target[0] < grid.shape[0] \
                and 0 <= target[1] < grid.shape[1] \
                and (len(path) < 3 or set(direction) != set(last_directions)) \
                and (offset != -directions[path[-1]]).any():

                # don't reverse direction
                assert not ((direction == "l") and (path[-1] == "r"))
                assert not ((direction == "r") and (path[-1] == "l"))
                assert not ((direction == "u") and (path[-1] == "d"))
                assert not ((direction == "d") and (path[-1] == "u"))
                
                # valid step to take, no check if we should continue investigating this step
                target_idx = tuple(target)
                new_heat_loss = heat_loss + grid[target_idx]
                new_last_directions = last_directions[-2:] + direction
                assert len(new_last_directions) <= 3
                assert len(new_last_directions) >= len(last_directions)
                shortest_elements = shortest[target_idx[0]][target_idx[1]]
                new_last_directions_subs = [new_last_directions[i:] for i in range(len(new_last_directions)-1)]
                if all([(new_last_directions_sub not in shortest_elements or shortest_elements[new_last_directions_sub][0] > new_heat_loss) for new_last_directions_sub in new_last_directions_subs]):
                    shortest_elements[new_last_directions] = (new_heat_loss, path + direction)
                    new_queue_elements.append((target, new_heat_loss, path + direction))




        print(pos, new_queue_elements)
        queue += new_queue_elements
            


    return min(shortest[-1][-1].values(), key=lambda x: x[0])[0]


assert day_17_part_1("input_day_17_test2") == 5, day_17_part_1("input_day_17_test2")
assert day_17_part_1("input_day_17_test1") == 102, day_17_part_1("input_day_17_test1")

solution = day_17_part_1("input_day_17")
print("Solution Day 17 Part 1", solution)
# assert solution == 102, solution

[0 1] [(array([1, 1]), 6, 'rd')]
[1 0] [(array([1, 1]), 5, 'dr')]
[1 1] [(array([1, 0]), 9, 'rdl')]
[1 1] [(array([0, 1]), 9, 'dru')]
[1 0] [(array([0, 0]), 11, 'rdlu')]
[0 1] [(array([0, 0]), 11, 'drul')]
[0 0] [(array([0, 1]), 15, 'rdlur')]
[0 0] [(array([1, 0]), 14, 'druld')]
[0 1] [(array([1, 1]), 17, 'rdlurd')]
[1 0] [(array([1, 1]), 16, 'druldr')]
[1 1] []
[1 1] []
[0 1] [(array([0, 2]), 5, 'rr'), (array([1, 1]), 6, 'rd')]
[1 0] [(array([1, 1]), 5, 'dr'), (array([2, 0]), 6, 'dd')]
[0 2] [(array([0, 3]), 8, 'rrr'), (array([1, 2]), 6, 'rrd')]
[1 1] [(array([1, 2]), 7, 'rdr'), (array([1, 0]), 9, 'rdl'), (array([2, 1]), 8, 'rdd')]
[1 1] [(array([1, 2]), 6, 'drr'), (array([2, 1]), 7, 'drd'), (array([0, 1]), 9, 'dru')]
[2 0] [(array([2, 1]), 8, 'ddr'), (array([3, 0]), 9, 'ddd')]
[0 3] [(array([1, 3]), 13, 'rrrd')]
[1 2] [(array([1, 3]), 11, 'rrdr'), (array([1, 1]), 8, 'rrdl'), (array([2, 2]), 11, 'rrdd')]
[1 2] [(array([1, 3]), 12, 'rdrr'), (array([2, 2]), 12, 'rdrd'), (array([0, 2]), 

[2 5] []
[0 5] []
[0 7] []
[0 5] []
[3 8] []
[4 7] []
[2 7] []
[4 7] []
[4 5] []
[5 6] [(array([6, 6]), 57, 'rrrdrdrdrddd')]
[2 7] [(array([2, 8]), 52, 'rrrdrdrdrurr'), (array([3, 7]), 55, 'rrrdrdrdrurd'), (array([1, 7]), 52, 'rrrdrdrdruru')]
[2 5] [(array([2, 4]), 47, 'rrrdrdrdrull'), (array([3, 5]), 53, 'rrrdrdrdruld'), (array([1, 5]), 50, 'rrrdrdrdrulu')]
[1 6] [(array([1, 7]), 49, 'rrrdrdrdruur'), (array([1, 5]), 49, 'rrrdrdrdruul'), (array([0, 6]), 46, 'rrrdrdrdruuu')]
[3 2] []
[4 3] []
[2 3] []
[4 5] []
[4 3] []
[5 4] []
[2 5] []
[2 3] []
[1 4] []
[4 7] [(array([4, 8]), 57, 'rrrdrdrddrrr'), (array([5, 7]), 58, 'rrrdrdrddrrd'), (array([3, 7]), 59, 'rrrdrdrddrru')]
[5 6] [(array([5, 7]), 58, 'rrrdrdrddrdr'), (array([5, 5]), 60, 'rrrdrdrddrdl'), (array([6, 6]), 57, 'rrrdrdrddrdd')]
[3 6] [(array([3, 7]), 56, 'rrrdrdrddrur'), (array([3, 5]), 56, 'rrrdrdrddrul'), (array([2, 6]), 53, 'rrrdrdrddruu')]
[4 3] [(array([4, 2]), 52, 'rrrdrdrddlll'), (array([5, 3]), 56, 'rrrdrdrddlld'), (arra